In [1]:
!pip install bs4 requests

In [2]:
import os
import json
import rasterio
import requests
import bs4 as BeautifulSoup

from concurrent import futures
from rasterio.warp import transform_bounds

import bs4 as BeautifulSoup

In [3]:
url = "https://www.digitalglobe.com/ecosystem/open-data/puerto-rico-earthquake"

# Read Page
r = requests.get(url)
soup = BeautifulSoup.BeautifulSoup(r.text)
s = soup.findAll('a')

In [4]:
list_file = list(set([l.get('href') for l in s if  l.get('href').endswith(".tif")]))

files = [
    dict(
        date=l.split("/")[6],
        tags=[l.split("/")[5]],
        path=l,
        sceneid=l.split("/")[7],
        preview=f"https://api.discover.digitalglobe.com/show?id={l.split('/')[7]}&f=jpeg",
        event=l.split("/")[4],
    )
    for l in list_file
]

print(len(list_file))
print(files)

59
[{'date': '2019-11-30', 'tags': ['pre-event'], 'path': 'https://opendata.digitalglobe.com/events/puerto-rico-earthquake/pre-event/2019-11-30/105001001A163800/105001001A163800.tif', 'sceneid': '105001001A163800', 'preview': 'https://api.discover.digitalglobe.com/show?id=105001001A163800&f=jpeg', 'event': 'puerto-rico-earthquake'}, {'date': '2019-03-14', 'tags': ['pre-event'], 'path': 'https://opendata.digitalglobe.com/events/puerto-rico-earthquake/pre-event/2019-03-14/103001008C7A2B00/103001008C7A2B00.tif', 'sceneid': '103001008C7A2B00', 'preview': 'https://api.discover.digitalglobe.com/show?id=103001008C7A2B00&f=jpeg', 'event': 'puerto-rico-earthquake'}, {'date': '2019-10-12', 'tags': ['pre-event'], 'path': 'https://opendata.digitalglobe.com/events/puerto-rico-earthquake/pre-event/2019-10-12/103001009BC75100/103001009BC75100.tif', 'sceneid': '103001009BC75100', 'preview': 'https://api.discover.digitalglobe.com/show?id=103001009BC75100&f=jpeg', 'event': 'puerto-rico-earthquake'}, {'d

In [5]:
def worker(meta):
    try:

        with rasterio.open(meta["path"]) as src:
            wgs_bounds = transform_bounds(*[src.crs, 'epsg:4326'] + list(src.bounds), densify_pts=21)

        return {
            "geometry": {
                "type": "Polygon",
                "coordinates": [
                    [
                        [wgs_bounds[0], wgs_bounds[3]],
                        [wgs_bounds[0], wgs_bounds[1]],
                        [wgs_bounds[2], wgs_bounds[1]],
                        [wgs_bounds[2], wgs_bounds[3]],
                        [wgs_bounds[0], wgs_bounds[3]]
                    ]
                ]
            },
            "properties": meta,
            "type": "Feature"
        }
    
    except:
        return {}

    
with futures.ThreadPoolExecutor(max_workers=5) as executor:
    responses = executor.map(worker, files)
    
files = [f for f in responses if f]

In [6]:
geojson = {'type': 'FeatureCollection', 'features': files}

In [7]:
with open("PuertoRico_2020.geojson", "w") as f:
    f.write(json.dumps(geojson))

In [8]:
len(files)

59

In [9]:
files

[{'geometry': {'type': 'Polygon',
   'coordinates': [[[-66.43524128578582, 18.08013952445195],
     [-66.43524128578582, 18.019436192521077],
     [-66.27830499479575, 18.019436192521077],
     [-66.27830499479575, 18.08013952445195],
     [-66.43524128578582, 18.08013952445195]]]},
  'properties': {'date': '2019-11-30',
   'tags': ['pre-event'],
   'path': 'https://opendata.digitalglobe.com/events/puerto-rico-earthquake/pre-event/2019-11-30/105001001A163800/105001001A163800.tif',
   'sceneid': '105001001A163800',
   'preview': 'https://api.discover.digitalglobe.com/show?id=105001001A163800&f=jpeg',
   'event': 'puerto-rico-earthquake'},
  'type': 'Feature'},
 {'geometry': {'type': 'Polygon',
   'coordinates': [[[-66.84360614624897, 18.12994464978992],
     [-66.84360614624897, 17.912560992826027],
     [-66.68735714729962, 17.912560992826027],
     [-66.68735714729962, 18.12994464978992],
     [-66.84360614624897, 18.12994464978992]]]},
  'properties': {'date': '2019-03-14',
   'tags'